# M1. Actividad - Agente Aspiradora

**Jessica Nicole Copado Leal - A01637876**

In [1]:
# Import libraries

# Model design
import agentpy as ap

# Visualization
import matplotlib.pyplot as plt
import seaborn as sns
import IPython
import random

In [2]:
# Class that models the vacuum simulation with three phases: 
# 1. The initial setup of the agents and the environment
# 2. The process of vacumming depending on the condition (0, 1, 2)
# 3. The final process that checks whether it's done vacuuming

class Vacuum(ap.Model):

    def setup(self):

        # Create agents (tiles and vacuums)
        n_vacuums = int(self.p['Number of vacuum cleaners'])
        n_dirtyTiles = int(self.p['Dirty tiles percentage'] * (self.p.size**2))
        
        vacuums = self.vacuumAgents = ap.AgentList(self, n_vacuums)
        dirtyTiles = self.dirtyTilesAgents = ap.AgentList(self, self.p.size**2)

        # Initiate a dynamic variable for all agents
        # Condition 0: Dirty, 1: Clean, 2: Vacuum
        dirtyTiles.condition = 1
        dirtiness = dirtyTiles.random(n_dirtyTiles)
        dirtiness.condition = 0
      
        vacuums.condition = 2
        coordinate = (1,1)
        coordinates = [coordinate] * n_vacuums
        
        # Create grid (room)
        self.room = ap.Grid(self, [self.p.size]*2, track_empty=True)
        self.room.add_agents(dirtyTiles, random=True, empty=True)
        self.room.add_agents(vacuums, positions=coordinates, empty= True)


    def step(self):
        # Select tile being cleaned
        vacuumPositions = self.vacuumAgents.select(self.vacuumAgents.condition == 2)
        self.vacuumCleanerMovements = 0
        
        # Cleaning process
        for cleaner in vacuumPositions:
            for neighbor in self.room.neighbors(cleaner, distance=0):
                self.vacuumCleanerMovements += 1
                if neighbor.condition == 0:
                    neighbor.condition = 1
                if neighbor.condition == 2:
                    pass
            self.room.move_by(cleaner,(random.randrange(-1,2),random.randrange(-1,2)))
        
        dirtiness = self.dirtyTilesAgents.select(self.dirtyTilesAgents.condition == 0)

        # Stop simulation if all tiles are cleaned
        if len(dirtiness) == 0:
            cleaned_tiles = len(self.dirtyTilesAgents.select(self.dirtyTilesAgents.condition == 1))
            self.report('Percentage of cleaned tiles', cleaned_tiles / len(self.dirtyTilesAgents))
            self.report('Steps', model.t)
            self.report('Movements', model.vacuumCleanerMovements) 
            self.stop()  

    def end(self):

        # Document a measure at the end of the simulation
        cleaned_tiles = len(self.dirtyTilesAgents.select(self.dirtyTilesAgents.condition == 1))
        self.report('Percentage of cleaned tiles', cleaned_tiles / len(self.dirtyTilesAgents))
        self.report('Steps', model.t)
        self.report('Movements', model.vacuumCleanerMovements) 
        

In [3]:
# Define parameters

parameters = {
    'Number of vacuum cleaners': 200,
    'Dirty tiles percentage': 0.7, # Percentage of grid covered by dirt
    'size': 40, # Height and length of the room
    'steps': 300,
}

In [4]:
# Create single-run animation with custom colors

def animation_plot(model, ax):
    attr_grid = model.room.attr_grid('condition')
    color_dict = {0:'#808080', 2:'#fff2cc', 1:'#ffffff', None:'#eeeeee'}
    ap.gridplot(attr_grid, ax=ax, color_dict=color_dict, convert=True)
    ax.set_title(f"Simulation of a vacuum cleaner in a room\n"
                 f"Time-step: {model.t}, Tiles left to be cleaned: "
                 f"{len(model.dirtyTilesAgents.select(model.dirtyTilesAgents.condition == 0))}")

fig, ax = plt.subplots()
model = Vacuum(parameters)
model.record(model.vars)
animation = ap.animate(model, fig, ax, animation_plot)
IPython.display.HTML(animation.to_jshtml(fps=60))

In [5]:
model.reporters

{'seed': 63858582107471590047477320044882636249}

In [ ]:
# Change in parameters to obtain different outcomes

# Prepare parameter sample
parameters = {
    'Number of vacuum cleaners': 40,
    'Dirty tiles percentage': ap.Range(0.3, 0.6), # Percentage of grid covered by dirt
    'size': 30, # Height and length of the room
    'steps': 300,
}
sample = ap.Sample(parameters, n=20)

# Perform experiment
exp = ap.Experiment(Vacuum, sample, iterations=20)
results = exp.run()

Scheduled runs: 400
Completed: 159, estimated time remaining: 0:01:18

In [ ]:
# Plot sensitivity
sns.set_theme()
sns.lineplot(
    data=results.arrange_reporters(),
    x='Dirty tiles percentage',
    y='Percentage of cleaned tiles'
);